# Daten-Analyse Spaceship Titanic

In [1]:
import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
import joblib
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn import tree
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.ensemble import RandomForestRegressor
from sklearn.pipeline import make_pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.preprocessing import OneHotEncoder
from sklearn.metrics import accuracy_score



# Load CSV into Dataframe from Data folder
df = pd.read_csv('data/train.csv')
df_test = pd.read_csv('data/test.csv')

In [2]:
print(df.head())

  PassengerId HomePlanet CryoSleep  Cabin  Destination   Age    VIP  \
0     0001_01     Europa     False  B/0/P  TRAPPIST-1e  39.0  False   
1     0002_01      Earth     False  F/0/S  TRAPPIST-1e  24.0  False   
2     0003_01     Europa     False  A/0/S  TRAPPIST-1e  58.0   True   
3     0003_02     Europa     False  A/0/S  TRAPPIST-1e  33.0  False   
4     0004_01      Earth     False  F/1/S  TRAPPIST-1e  16.0  False   

   RoomService  FoodCourt  ShoppingMall     Spa  VRDeck               Name  \
0          0.0        0.0           0.0     0.0     0.0    Maham Ofracculy   
1        109.0        9.0          25.0   549.0    44.0       Juanna Vines   
2         43.0     3576.0           0.0  6715.0    49.0      Altark Susent   
3          0.0     1283.0         371.0  3329.0   193.0       Solam Susent   
4        303.0       70.0         151.0   565.0     2.0  Willy Santantines   

   Transported  
0        False  
1         True  
2        False  
3        False  
4         True  


In [3]:
print(df.shape)

(8693, 14)


In [4]:
print(df.describe())

               Age   RoomService     FoodCourt  ShoppingMall           Spa  \
count  8514.000000   8512.000000   8510.000000   8485.000000   8510.000000   
mean     28.827930    224.687617    458.077203    173.729169    311.138778   
std      14.489021    666.717663   1611.489240    604.696458   1136.705535   
min       0.000000      0.000000      0.000000      0.000000      0.000000   
25%      19.000000      0.000000      0.000000      0.000000      0.000000   
50%      27.000000      0.000000      0.000000      0.000000      0.000000   
75%      38.000000     47.000000     76.000000     27.000000     59.000000   
max      79.000000  14327.000000  29813.000000  23492.000000  22408.000000   

             VRDeck  
count   8505.000000  
mean     304.854791  
std     1145.717189  
min        0.000000  
25%        0.000000  
50%        0.000000  
75%       46.000000  
max    24133.000000  


In [5]:
print(df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8693 entries, 0 to 8692
Data columns (total 14 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   PassengerId   8693 non-null   object 
 1   HomePlanet    8492 non-null   object 
 2   CryoSleep     8476 non-null   object 
 3   Cabin         8494 non-null   object 
 4   Destination   8511 non-null   object 
 5   Age           8514 non-null   float64
 6   VIP           8490 non-null   object 
 7   RoomService   8512 non-null   float64
 8   FoodCourt     8510 non-null   float64
 9   ShoppingMall  8485 non-null   float64
 10  Spa           8510 non-null   float64
 11  VRDeck        8505 non-null   float64
 12  Name          8493 non-null   object 
 13  Transported   8693 non-null   bool   
dtypes: bool(1), float64(6), object(7)
memory usage: 891.5+ KB
None


In [6]:
# use one hot encoding to convert categorical columns to numeric
df_cats = df.select_dtypes(include='object')
one_hot = OneHotEncoder()
df_cats = one_hot.fit_transform(df_cats).toarray()
df_cats = pd.DataFrame(df_cats, columns=one_hot.get_feature_names_out())
df_cats

PassengerId_0001_01  PassengerId_0002_01  PassengerId_0003_01  \
0                     1.0                  0.0                  0.0   
1                     0.0                  1.0                  0.0   
2                     0.0                  0.0                  1.0   
3                     0.0                  0.0                  0.0   
4                     0.0                  0.0                  0.0   
...                   ...                  ...                  ...   
8688                  0.0                  0.0                  0.0   
8689                  0.0                  0.0                  0.0   
8690                  0.0                  0.0                  0.0   
8691                  0.0                  0.0                  0.0   
8692                  0.0                  0.0                  0.0   

      PassengerId_0003_02  PassengerId_0004_01  PassengerId_0005_01  \
0                     0.0                  0.0                  0.0   
1                     0.0                  0.0                  0.0   
2                     0.0                  0.0                  0.0   
3                     1.0                  0.0                  0.0   
4                     0.0                  1.0                  0.0   
...                   ...                  ...                  ...   
8688                  0.0                  0.0                  0.0   
8689                  0.0                  0.0                  0.0   
8690                  0.0                  0.0                  0.0   
8691                  0.0                  0.0                  0.0   
8692                  0.0                  0.0                  0.0   

      PassengerId_0006_01  PassengerId_0006_02  PassengerId_0007_01  \
0                     0.0                  0.0                  0.0   
1                     0.0                  0.0                  0.0   
2                     0.0                  0.0                  0.0   
3                     0.0                  0.0                  0.0   
4                     0.0                  0.0                  0.0   
...                   ...                  ...                  ...   
8688                  0.0                  0.0                  0.0   
8689                  0.0                  0.0                  0.0   
8690                  0.0                  0.0                  0.0   
8691                  0.0                  0.0                  0.0   
8692                  0.0                  0.0                  0.0   

      PassengerId_0008_01  ...  Name_Zinor Axlentindy  Name_Zinor Proorbeng  \
0                     0.0  ...                    0.0                   0.0   
1                     0.0  ...                    0.0                   0.0   
2                     0.0  ...                    0.0                   0.0   
3                     0.0  ...                    0.0                   0.0   
4                     0.0  ...                    0.0                   0.0   
...                   ...  ...                    ...                   ...   
8688                  0.0  ...                    0.0                   0.0   
8689                  0.0  ...                    0.0                   0.0   
8690                  0.0  ...                    0.0                   0.0   
8691                  0.0  ...                    0.0                   0.0   
8692                  0.0  ...                    0.0                   0.0   

      Name_Zinoth Lansuffle  Name_Zosmark Trattle  Name_Zosmark Unaasor  \
0                       0.0                   0.0                   0.0   
1                       0.0                   0.0                   0.0   
2                       0.0                   0.0                   0.0   
3                       0.0                   0.0                   0.0   
4                       0.0                   0.0                   0.0   
...                     ...                   ..

In [7]:
# drop categorical columns from original dataframe
df = df.drop(columns=df.select_dtypes(include='object').columns)
df = pd.concat([df, df_cats], axis=1)
df

Age  RoomService  FoodCourt  ShoppingMall     Spa  VRDeck  Transported  \
0     39.0          0.0        0.0           0.0     0.0     0.0        False   
1     24.0        109.0        9.0          25.0   549.0    44.0         True   
2     58.0         43.0     3576.0           0.0  6715.0    49.0        False   
3     33.0          0.0     1283.0         371.0  3329.0   193.0        False   
4     16.0        303.0       70.0         151.0   565.0     2.0         True   
...    ...          ...        ...           ...     ...     ...          ...   
8688  41.0          0.0     6819.0           0.0  1643.0    74.0        False   
8689  18.0          0.0        0.0           0.0     0.0     0.0        False   
8690  26.0          0.0        0.0        1872.0     1.0     0.0         True   
8691  32.0          0.0     1049.0           0.0   353.0  3235.0        False   
8692  44.0        126.0     4688.0           0.0     0.0    12.0         True   

      PassengerId_0001_01  PassengerId_0002_01  PassengerId_0003_01  ...  \
0                     1.0                  0.0                  0.0  ...   
1                     0.0                  1.0                  0.0  ...   
2                     0.0                  0.0                  1.0  ...   
3                     0.0                  0.0                  0.0  ...   
4                     0.0                  0.0                  0.0  ...   
...                   ...                  ...                  ...  ...   
8688                  0.0                  0.0                  0.0  ...   
8689                  0.0                  0.0                  0.0  ...   
8690                  0.0                  0.0                  0.0  ...   
8691                  0.0                  0.0                  0.0  ...   
8692                  0.0                  0.0                  0.0  ...   

      Name_Zinor Axlentindy  Name_Zinor Proorbeng  Name_Zinoth Lansuffle  \
0                       0.0                   0.0                    0.0   
1                       0.0                   0.0                    0.0   
2                       0.0                   0.0                    0.0   
3                       0.0                   0.0                    0.0   
4                       0.0                   0.0                    0.0   
...                     ...                   ...                    ...   
8688                    0.0                   0.0                    0.0   
8689                    0.0                   0.0                    0.0   
8690                    0.0                   0.0                    0.0   
8691                    0.0                   0.0                    0.0   
8692                    0.0                   0.0                    0.0   

      Name_Zosmark Trattle  Name_Zosmark Unaasor  Name_Zosmas Ineedeve  \
0                      0.0                   0.0                   0.0   
1                      0.0                   0.0                   0.0   
2                      0.0                   0.0                   0.0   
3                      0.0                   0.0                   0.0   
4                      0.0                   0.0                   0.0   
...                    ...                   ...                   ...   
8688                   0.0                   0.0                   0.0   
8689                   0.0                   0.0                   0.0   
8690                   0.0                   0.0                   0.0   
8691                   0.0                   0.0                   0.0   
8692                   0.0                   0.0                   0.0   

      Name_Zosmas Mormonized  Name_Zubeneb Flesping  Name_Zubeneb Pasharne  \
0                        0.0                    0.0                    0.0   
1                        0.0                    0.0                    0.0   
2                        0.0                    0.0                    0.0   
3      

In [8]:
# Show me all columns
pd.set_option('display.max_columns', None)
df.head()


Age  RoomService  FoodCourt  ShoppingMall     Spa  VRDeck  Transported  \
0  39.0          0.0        0.0           0.0     0.0     0.0        False   
1  24.0        109.0        9.0          25.0   549.0    44.0         True   
2  58.0         43.0     3576.0           0.0  6715.0    49.0        False   
3  33.0          0.0     1283.0         371.0  3329.0   193.0        False   
4  16.0        303.0       70.0         151.0   565.0     2.0         True   

   PassengerId_0001_01  PassengerId_0002_01  PassengerId_0003_01  \
0                  1.0                  0.0                  0.0   
1                  0.0                  1.0                  0.0   
2                  0.0                  0.0                  1.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   PassengerId_0003_02  PassengerId_0004_01  PassengerId_0005_01  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  1.0                  0.0                  0.0   
4                  0.0                  1.0                  0.0   

   PassengerId_0006_01  PassengerId_0006_02  PassengerId_0007_01  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   PassengerId_0008_01  PassengerId_0008_02  PassengerId_0008_03  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   PassengerId_0009_01  PassengerId_0010_01  PassengerId_0011_01  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   PassengerId_0012_01  PassengerId_0014_01  PassengerId_0015_01  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   PassengerId_0016_01  PassengerId_0017_01  PassengerId_0017_02  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   PassengerId_0020_01  PassengerId_0020_02  PassengerId_0020_03  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                  0.0   
3                  0.0                  0.0                  0.0   
4                  0.0                  0.0                  0.0   

   PassengerId_0020_04  PassengerId_0020_05  PassengerId_0020_06  \
0                  0.0                  0.0                  0.0   
1                  0.0                  0.0                  0.0   
2                  0.0                  0.0                

In [9]:
# Show me all columns with NaN values
df.columns[df.any()].tolist()


['Age',
 'RoomService',
 'FoodCourt',
 'ShoppingMall',
 'Spa',
 'VRDeck',
 'Transported',
 'PassengerId_0001_01',
 'PassengerId_0002_01',
 'PassengerId_0003_01',
 'PassengerId_0003_02',
 'PassengerId_0004_01',
 'PassengerId_0005_01',
 'PassengerId_0006_01',
 'PassengerId_0006_02',
 'PassengerId_0007_01',
 'PassengerId_0008_01',
 'PassengerId_0008_02',
 'PassengerId_0008_03',
 'PassengerId_0009_01',
 'PassengerId_0010_01',
 'PassengerId_0011_01',
 'PassengerId_0012_01',
 'PassengerId_0014_01',
 'PassengerId_0015_01',
 'PassengerId_0016_01',
 'PassengerId_0017_01',
 'PassengerId_0017_02',
 'PassengerId_0020_01',
 'PassengerId_0020_02',
 'PassengerId_0020_03',
 'PassengerId_0020_04',
 'PassengerId_0020_05',
 'PassengerId_0020_06',
 'PassengerId_0022_01',
 'PassengerId_0024_01',
 'PassengerId_0025_01',
 'PassengerId_0026_01',
 'PassengerId_0028_01',
 'PassengerId_0030_01',
 'PassengerId_0031_01',
 'PassengerId_0031_02',
 'PassengerId_0031_03',
 'PassengerId_0034_01',
 'PassengerId_0035_01'

In [10]:
# Fill NaN of each column with mean of that column
for col in df.columns[df.any()].tolist():
    df[col] = df[col].fillna(df[col].mean())



In [11]:
# show how many nan values are in each column
print(df.isnull().sum())

Age                       0
RoomService               0
FoodCourt                 0
ShoppingMall              0
Spa                       0
                         ..
Name_Zosmas Ineedeve      0
Name_Zosmas Mormonized    0
Name_Zubeneb Flesping     0
Name_Zubeneb Pasharne     0
Name_nan                  0
Length: 23749, dtype: int64


In [12]:
y = df["Transported"]
X = df.drop('Transported', axis=1)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=123, stratify=y)

In [13]:
rf = RandomForestClassifier(n_estimators=50, max_leaf_nodes=50, random_state=42)
rf.fit(X_train, y_train)
y_pred = rf.predict(X_test)
Random_Forest = ('Accuracy score: ', accuracy_score(y_test, y_pred))
print(Random_Forest)

: 

In [ ]:
ada = AdaBoostClassifier(n_estimators=250, random_state=42)
ada.fit(X_train, y_train)
y_pred = ada.predict(X_test)
ADA_Boost = print('Accuracy score: ', accuracy_score(y_test, y_pred))
print(ADA_Boost)

Accuracy score:  0.7901092581943646
None


In [ ]:
# Voting Classifier with rf and ada
from sklearn.ensemble import VotingClassifier
voting_clf = VotingClassifier(
    estimators=[('rf', rf), ('ada', ada)],
    voting='hard')
voting_clf.fit(X_train, y_train)
y_pred = voting_clf.predict(X_test)
Voting_Classifier = print('Accuracy score: ', accuracy_score(y_test, y_pred))
print(Voting_Classifier)
